In [ ]:
from google.colab import files
files.upload()

Saving post_vaccination_twitter_data.csv to post_vaccination_twitter_data.csv


{'post_vaccination_twitter_data.csv': b'2021-03-16 23:59:58,1371974553161850884,b\'It would be hard for the Covid vaccine site I was at today to be better run. Just a model of efficacy.\'\r\n2021-03-16 23:59:54,1371974536980144131,"b""Report in NEJM today, AZ vaccine \'did not show protection against mild-to-moderate Covid-19 due to the B.1.351 vari\\xe2\\x80\\xa6 https://t.co/qzdQIhJUOP"""\r\n2021-03-16 23:59:47,1371974507896872961,b\'@boohoo07221632 @somedeadacc3 @jilliandawncla1 @msnorthcott @jaipo I...what part of I search instead of get fed new\\xe2\\x80\\xa6 https://t.co/yycJmuLTFg\'\r\n2021-03-16 23:59:42,1371974487416172550,b\'Finally going to be eligible for the covid vaccine this weekend \\xf0\\x9f\\x91\\x8f\\xf0\\x9f\\x8f\\xbe\\xf0\\x9f\\x91\\x8f\\xf0\\x9f\\x8f\\xbe\\xf0\\x9f\\x91\\x8f\\xf0\\x9f\\x8f\\xbe\'\r\n2021-03-16 23:59:40,1371974479736270848,"b\'Trump encourages Americans to get the Covid vaccine. Pretty wishy washy about it, but he did it.  https://t.co/wZZch57yHf v

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install transformers

     |████████████████████████████████| 2.1MB 7.9MB/s 
     |████████████████████████████████| 3.3MB 54.5MB/s 
     |████████████████████████████████| 901kB 38.1MB/s 


In [ ]:
import torch
if torch.cuda.is_available():       
    device = torch.device("cuda")
    print(f'There are {torch.cuda.device_count()} GPU(s) available.')
    print('Device name:', torch.cuda.get_device_name(0))

else:
    print('No GPU available, using the CPU instead.')
    device = torch.device("cpu")

There are 1 GPU(s) available.
Device name: Tesla T4


In [ ]:
import torch
import torch.nn as tor_nn
from transformers import BertModel

class ClassifierBert(tor_nn.Module):
  def __init__(self, freeze_bert=False):

    super (ClassifierBert,self).__init__()

    bert_hidden, classifier_hidden , output_labels = 768 , 64 , 3
    model_name = "bert_classifier.pt"
    path = F"/content/drive/My Drive/{model_name}"
    state_bert = torch.load(path)
    self.bert = BertModel.from_pretrained('bert-base-uncased',state_dict=state_bert)
    if freeze_bert:

      for parameter in self.bert.parameters():

        parameter.requires_grad=False

    self.dropout = tor_nn.Dropout(0.6)
    self.relu = tor_nn.ReLU()
    self.fc1 =  tor_nn.Linear(768,25)
    self.fc4 = tor_nn.Linear(25,3)
    self.softmax = tor_nn.LogSoftmax(dim=-1)

    

  def forward(self, input_ids, attention_mask):

    _,output = self.bert(input_ids=input_ids,attention_mask=attention_mask,return_dict=False)

    logits = self.fc1(output)

    logits=self.relu(logits)

    logits = self.dropout(logits)

    logits = self.fc4(logits)

    logits = self.softmax(logits)

   

   

    return logits

In [ ]:
def model_initialization(epochs=10):
  
  classifier_bert = ClassifierBert(freeze_bert = False)

  classifier_bert=classifier_bert.to(device)
 
  return classifier_bert

In [ ]:
bert_classifier = model_initialization()

In [ ]:
bert_classifier.eval()

ClassifierBert(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=Tru

In [ ]:
import pandas as pd
test_data = pd.read_csv('post_vaccination_twitter_data.csv',names=['created_at','id','text'])
test_df = pd.DataFrame(test_data)
del test_df['id']
del test_df['created_at']
data = list(test_df['text'])

In [ ]:
from transformers import BertTokenizer
model_name = "bert_classifier.pt"
path = F"/content/drive/My Drive/{model_name}"
state_bert = torch.load(path)
mytokenizer=BertTokenizer.from_pretrained('bert-base-uncased',do_lower=True,state_dict=state_bert)

test_input_id = []
test_attention_mask = []

test_df.dropna()
texts = test_df["text"].to_list()

for value in texts: 
 encode_sent_data = mytokenizer.encode_plus(text=str(value),truncation=True, add_special_tokens=True, max_length=35,pad_to_max_length=True,return_attention_mask=True)
 test_input_id.append(encode_sent_data.get('input_ids'))
 test_attention_mask.append(encode_sent_data.get('attention_mask'))

    
test_attention_mask = torch.tensor(test_attention_mask)  
test_input_id = torch.tensor(test_input_id)


/usr/local/lib/python3.7/dist-packages/transformers/tokenization_utils_base.py:2079: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  FutureWarning,


In [ ]:
from torch.utils.data import TensorDataset ,  DataLoader, RandomSampler, SequentialSampler
batch_size=1
test_data =  TensorDataset(test_input_id , test_attention_mask)
test_sampler = SequentialSampler(test_data)
test_dataloader = DataLoader(test_data , sampler = test_sampler, batch_size=batch_size)


In [ ]:
import numpy as np
def evaluate(model,testing_dataloader):
  model.eval()
  predictions,true_value = [],[]

  for batch in testing_dataloader:
    bert_input_ids , bert_attention_mask = tuple(t.to(device) for t in batch)
    with torch.no_grad():
      logits = model(bert_input_ids,bert_attention_mask)
       
    logits = logits.detach().cpu().numpy()
   
    predictions.append(logits)
    
 
  predictions = np.concatenate(predictions ,axis=0)
 
  return predictions



In [ ]:
predictions = evaluate(bert_classifier,test_dataloader)

In [ ]:
predictions = torch.tensor(predictions)
pred=torch.exp(predictions).numpy()

In [ ]:
label=[]
for data in pred:
  label.append(data.argmax())
#print(label)
test_df['label'] = list(label)

In [ ]:
test_df.to_csv('predicted_post_covid.csv')